## 1. Generátory, řády

In [2]:
F = GF(1009)

In [3]:
F.primitive_element()

11

In [11]:
F(158).is_primitive_root()

True

In [7]:
F(2).multiplicative_order()

504

In [9]:
# pozor, toto by byl řád ve sčítací grupě!
F(2).order()

1009

In [37]:
# počet prim. prvků se spočte Eulerovou funkcí
# (jelikož víme, že multiplikativní grupa je cyklická)
euler_phi(F.unit_group_order())

288

## 2. FFT

In [15]:
# omega = primitivní n-tá odmocnina z 1
# coeffs = list s koeficienty polynomu 
#          (může být i přímo polynom díky přetypování)

def FFT(omega, coeffs):
    coeffs = list(coeffs)
    clen = len(coeffs)
    if clen == 1:
        # tak, jak je to napsáno ve skriptech, se tady vrací přímo to číslo,
        # ale ve skutečnosti chceme jednoprvkový list obsahující ono číslo
        return coeffs
    half_len = len(coeffs)//2
    omega_sq = omega^2
    # coeffs[::2], coeffs[1::2] = prvky listu na sudých a lichých pozicích
    bs = FFT(omega_sq, coeffs[::2])
    cs = FFT(omega_sq, coeffs[1::2])
    reta = []
    retb = []
    omega_pow = 1
    for b, c in zip(bs, cs):
        reta.append(b + omega_pow*c)
        retb.append(b - omega_pow*c)
        omega_pow *= omega
    return reta + retb

In [16]:
P.<x> = GF(257)[]
f = 7*x^7+14*x^2+5

In [20]:
p = GF(257).primitive_element()

# p je generátor, takže prim. 256-tá odmocnina z 1
# pro prim. osmou odmocninu umocníme na 256/8 = 32
omega = p^32
print(omega)
print(omega.multiplicative_order())

64
8


In [19]:
FFT(omega, f)

[26, 10, 103, 38, 12, 66, 136, 163]

In [38]:
#pro kontrolu:
[f(omega^i) for i in range(8)]

[26, 10, 103, 38, 12, 66, 136, 163]

## 3. Inverzní FFT

In [28]:
# IFFT je pouze FFT s inverzní odmocninou, kde navíc dělíme "n",
# přičemž pro toto dělení musíme vzít n v rámci
# správného okruhu (tím je omega.parent())

def IFFT(omega,coeffs):
    one_over_n = (omega.parent()(len(coeffs)))^(-1)
    return [one_over_n*el for el in FFT(omega^(-1), coeffs)] 

In [29]:
P(IFFT(omega, [26, 10, 103, 38, 12, 66, 136, 163]))

7*x^7 + 14*x^2 + 5

## 4. Násobení v $\mathbb Z[x]$ pomocí FFT

In [42]:
"""Funkce pro násobení dvou celočíselných polynomů za použítí komplexních odmocnin z 1
-- f, g: libovolné polynomy
-- prec: počet bitů s jejichž přesností se počítá v komplexních číslech
"""
def mul_complex(f, g, prec = 64):
    C = ComplexField(prec)
    # jak velké pole budeme potřebovat pro výsledek?
    # jeho stupeň bude součet stupňů, koeficientů je
    # o 1 víc než stupeň, k tomuto chceme vzít nejbližší
    # mocninu dvojky
    f_deg, g_deg = (p.degree() for p in (f, g))
    n = f_deg + g_deg
    n = 1 << n.nbits()
    
    f_coeffs = list(f) + [0] * (n-f_deg-1) # doplní nulami koeficienty f a g do počtu n 
    g_coeffs = list(g) + [0] * (n-g_deg-1)
    omega = C(e^(2*pi*I/n)) # prim. n-tá odmocnina z 1
    F = FFT(omega, f_coeffs)
    G = FFT(omega, g_coeffs)
    RES = [ff*gg for ff, gg in zip(F, G)]
    res = IFFT(omega, RES)
    res = [el.real().round() for el in res] # vezme z komplexního čísla reálnou část a zaokrouhlí ji na nejbližší celé číslo
    return f.parent(res) # převede koeficienty zpátky do polynomu z původního oboru (ten je = f.parent())

In [72]:
# zkouška -- při malé přesnosti (10) někdy vyjde správný výsledek,
# někdy ne, pro 20 už snad vždy ano
Q.<t> = ZZ[]
prec = 10
f = Q.random_element(degree=10)
g = Q.random_element(degree=10)
print(f"polynom f: {f}")
print(f"polynom g: {g}")
a = mul_complex(f, g, prec=prec)
b = f*g
print(a)
print(b)
print(a==b)


polynom f: -2*t^10 + t^8 + t^7 - 2*t^6 + 2*t^5 - 3*t^4 + t^3 - t^2 + 4*t + 1
polynom g: 2*t^10 - 2*t^9 + t^8 + 24*t^7 - 9*t^6 + 2*t^4 + 1
-4*t^20 + 4*t^19 - 48*t^17 + 13*t^16 + 33*t^15 - t^14 - 47*t^13 + 61*t^12 - 77*t^11 + 38*t^10 - 27*t^9 + 100*t^8 - 9*t^7 - 13*t^6 + 10*t^5 - t^4 + t^3 - t^2 + 4*t + 1
-4*t^20 + 4*t^19 - 48*t^17 + 13*t^16 + 33*t^15 - t^14 - 47*t^13 + 61*t^12 - 77*t^11 + 38*t^10 - 27*t^9 + 101*t^8 - 9*t^7 - 13*t^6 + 10*t^5 - t^4 + t^3 - t^2 + 4*t + 1
False


## 5. Násobení v $\mathbb Q[x]$

In [74]:
# Vynásobí dva racionální polynomy za pomocí komplexní odmocniny z 1 a FFT
def fast_mul_rat(f, g, prec=64):
    # denominator vrátí NSN jmenovatelů koeficientů
    a = f.denominator()
    b = g.denominator()
    # přesuneme se do polynomů nad Z
    ff = (a*f).change_ring(ZZ)
    gg = (b*g).change_ring(ZZ)
    res = mul_complex(ff, gg, prec).change_ring(QQ)
    return res/(a*b)

In [77]:
# zkouška...
R.<s> = QQ[]
f = 1/3*s^3+1/6*s+1/5
g = 2*s^2+1/4
print(fast_mul_rat(f,g))
print(f*g)

2/3*s^5 + 5/12*s^3 + 2/5*s^2 + 1/24*s + 1/20
2/3*s^5 + 5/12*s^3 + 2/5*s^2 + 1/24*s + 1/20


## 6. Existence odmocnin z 1 a charakteristika

Nechť má těleso $\mathbb F$ charakteristiku $p$, dále nechť je $\omega$ primitivní $n$-tá odmocnina z $1$ a platí $p \mid n$. Potom $\zeta = \omega^{n/p}$ je primitivní $p$-tá odmocnina z $1$. Jelikož jsme v charakteristice $p$, platí
$$ (\zeta - 1)^p = \zeta^p - 1^p = 1 - 1 = 0, $$
ovšem protože jsme v tělese, toto implikuje $\zeta - 1 = 0$ neboli $\zeta = 1$, ovšem dle definice $\zeta \neq 1$ ($\zeta$ má řád $p$).

## 7. Horní odhad Eulera

Je-li $n$ sudé, pak $n = 2^k \cdot m$ pro $m$ liché a $k \in \mathbb N$. Z vlastností Eulerovy funkce pak plyne, že
$$ \varphi(n) = \varphi(2^k) \cdot \varphi(m) = 2^{k-1} \cdot \varphi(m), $$
takže
$$ \frac{\varphi(n)}{n} = \frac{2^{k-1} \cdot \varphi(m)}{2^k \cdot m} = \frac{\varphi(m)}{2 \cdot m} \leq \frac12, $$
jelikož $\varphi(m) \leq m$ pro $m > 0$. Rovnost nastává, když $\varphi(m) = m$, což je jen při $m = 1$, neboli když $n$ je mocnina dvojky.

## 8. Lim sup/inf Eulera

Je-li $p$ prvočíslo, pak $\varphi(p) = p-1$, takže pro $i$-té prvočíslo $p_i$ máme
$$ \frac{\varphi(p_i)}{p_i} = 1 - \frac{1}{p_i} \stackrel{i \to \infty}\longrightarrow 1, $$
takže (v kombinaci s $\varphi(n) \leq n$) dostáváme $\limsup \frac{\varphi(n)}{n} = 1$.

Je-li $n$ součin prvních $k$ prvočísel (tj. $n = p_1 \cdot p_2 \cdots p_k$), pak
$$ \frac{\varphi(n)}{n} = \prod_{i=1}^k \left(1 - \frac{1}{p_i}\right); $$
ukážeme, že tento součin konverguje k $0$, k čemuž nám stačí dokázat, že jeho logaritmus konverguje k $-\infty$;
řešíme tedy konvergenci řady
$$ \sum_{i-1}^\infty \log \left(1 - \frac{1}{p_i}\right). $$
Jelikož je $\lim_{x \to 0} \frac{\log(1+x)}{x} = 1$ a $\sum \frac1{p_i} = +\infty$, podle limitního srovnávacího kritéria je součet oné řady logaritmů $-\infty$, což jsme chtěli. Je tedy $\liminf \frac{\varphi(n)}{n} = 0$.